In [1]:
import pandas as pd 
import geopandas as gpd
from shapely.geometry import Point

In [2]:
# ACE Violations from 2023 Jul 01 12:00:00 AM to 2023 December 31 11:45:00 PM (6 Month Period)
df = pd.read_csv("Datasets/ACE_Violations_Jul-Dec2023.csv")

In [3]:
# Convert violations DataFrame → GeoDataFrame
gdf = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df["Violation Longitude"], df["Violation Latitude"]),
    crs="EPSG:4326"  # Tells geopandas how coordinates interperted on earth
)

In [4]:
# Loading in the boundaries for congestion zone in Central Business District
region = gpd.read_file("map.geojson")

In [5]:
# Getting the violations that are in congestion zone only
violations_in_region = gpd.sjoin(gdf, region, how="inner", predicate="within")

In [6]:
# Printing the basic information we can gather from this dataset
unique_buses = violations_in_region["Bus Route ID"].unique()
print("Total violations in dataset:", len(df))
print("Violations inside region:", len(violations_in_region))
print("Buses with violations in CBD:", unique_buses)
for bus in unique_buses:
    bus_violations = violations_in_region[violations_in_region["Bus Route ID"] == bus]
    print(f"Total violations on {bus} route: {len(bus_violations)}")

Total violations in dataset: 100847
Violations inside region: 5852
Buses with violations in CBD: ['M15+' 'M14+' 'M34+' 'M23+']
Total violations on M15+ route: 3938
Total violations on M14+ route: 1549
Total violations on M34+ route: 174
Total violations on M23+ route: 191


In [7]:
import folium

# Get the center of the region to focus the map
center_lat = violations_in_region["Violation Latitude"].mean()
center_lon = violations_in_region["Violation Longitude"].mean()

# Create a folium map
m = folium.Map(location=[center_lat, center_lon], zoom_start=14)

# Add polygon boundary (CBD)
folium.GeoJson("map.geojson", name="CBD").add_to(m)

# Add violations as points
for idx, row in violations_in_region.iterrows():
    folium.CircleMarker(
        location=[row["Violation Latitude"], row["Violation Longitude"]],
        radius=3,
        color='blue',
        fill=True,
        fill_opacity=0.5
    ).add_to(m)

# Display map
m